In [9]:
import math
import numpy as np

# Set sun, earth position
sun_mass = 1.98892 * 10**30
earth_mass = 5.9742 * 10**24
sun_to_earth = 1 # AU, check to make sure gravity is in AU

# Functions for computing gravity vectors
Gsc = 1.361 # kW/m2
A = 1 # m**2     # sail area
C_SRP    = 2.00 # SRP coefficent, C_SRP = 1 for perfectly absorbing, C_SRP = 2 for perfectly reflective  solar sail
# FN= 2GsccAcos2(α)≈(9μN/m2) cos2(α)

dim = 2 # 2 or 3d sim, starting with 2

# The gravitational constant G
G = 6.67428e-11

# Assumed scale: 100 pixels = 1AU.
AU = (149.6e6 * 1000)     # 149.6 million km, in meters.
SCALE = 250 / AU

# constants for inertial properties and torques
global r_ss, rp_ss, A_ss, Ap_ss, hp_ss, lp_ss, P_ss
r_ss = 0.56 #m, 
rp_ss = 0.565 #m
A_ss = 1 #m**2, 
Ap_ss = 0.02 #m**2
hp_ss = 10E-2 #m  
lp_ss = 20E-2 #m.
m_mp = 0.001 # kg (1gram)
m_ss = 0.0016 # kg (1.6grams)
mp_ss = 0.000032 # kg (32mg) 
P_ss = 9E-6 # uPa. (estimate)

# equations for roll flag control
# thetap_r = 2*math.asin(dyp_r/2/lp_ss)
# alphap_r = alpha - thetap_r

# Fp_s = f(alpha_roll, theta) = P_ss*Ap_ss*cos(alphap_r)**3
def Fp_s(alpha_r):
    return P_ss*Ap_ss*(math.cos(alpha_r)**2)

# F_s = f(alpha)  = P_ss*A_ss* cos(alpha)**3
def F_s(alpha_r):
    return P_ss*A_ss*(math.cos(alpha_r)**2)

# dx,dz in 0-10mm
#def T_yy(angle):
    # T_yy = Fp_s * rp_ss * math.sin(thetap_r) # = I_yy*theta_dot_dot

def T_zz(angle, dx):
    # T_zz = F_s*dx #  I_zz*alpha_dot_dot
    return F_s(angle)*dx

def T_xx(angle, dz):
    # T_xx = F_s*dz #  I_xx*alpha_dot_dot
    return F_s(angle)*dz

def inertials(dx,dy,dz,m_mp = 0.01, m_ss = 0.0014):
    ratio = m_mp/(m_ss+m_mp)
    x_ss = dx*ratio
    x_mp = dx*(1-ratio)
#     y_ss = dy*ratio
    y_tot = 2 #.05 # 2
    y_ss = y_tot*ratio
#     y_mp = dy*(1-ratio)
    y_mp = y_tot*(1-ratio)
    z_ss = dz*ratio
    z_mp = dz*(1-ratio)

    I_yy = 1 / 2 * m_ss * r_ss **2+ m_ss * (x_ss **2+ z_ss **2)+mp_ss * rp_ss **2+1 / 12 * mp_ss * hp_ss **2 + m_mp * (x_mp **2+z_mp**2)
    I_zz = 1 / 4 * m_ss * r_ss **2+m_ss * (x_ss **2+ y_ss **2)+m_mp * (x_mp**2+y_mp **2)
    I_xx = 1 / 4 * m_ss * r_ss **2+m_ss * (z_ss **2+ y_ss **2)+m_mp * (z_mp**2+y_mp **2)
    return I_xx, I_yy, I_zz

f = F_s(0)
n = 100
alpha = np.linspace(-np.pi/2,np.pi/2,n)
dx = np.linspace(-0.01,0.01,n)
dz = np.linspace(-0.01,0.01,n)
xx,zz = np.meshgrid(dx,dz)
rates = np.zeros((n,n,3))
for i, x in enumerate(dx):
    for j, a in enumerate(alpha):
        f = F_s(a)
        z = 0
        ix, iy, iz = inertials(x,0,z)
        tx = f *x #z
        ty = 0
        tz = f* z #x
        ox = tx/ix
        oy = 0
        oz = tz/iz
        rates[i,j,0] = ox
        rates[i,j,2] = oz 

        
import plotly.graph_objects as go

fig = go.Figure(data=go.Heatmap(
        z=rates[:,:,0],
        x=alpha,
        y=dx,
        colorscale='Viridis')
                )

fig.update_layout(
    title='Angular Rates vs Sun Angle vs Input',
    xaxis_title='cone angle (rad)',
    yaxis_title='input motion (m)')

fig.show()

In [10]:
import numpy as np

# PID controller for roll (add noise to simulation)
class PID():
    def __init__(self, desired,
                 kp, ki, kd,
                 ilimit, dt, outlimit=np.inf,
                 samplingRate=0, cutoffFreq=-1,
                 enableDFilter=False):

        # internal variables
        self.error = 0
        self.error_prev = 0
        self.integral = 0
        self.deriv = 0
        self.out = 0

        # constants
        self.desired = desired
        self.kp = kp
        self.ki = ki
        self.kd = kd

        # limits integral growth
        self.ilimit = ilimit

        # limits ridiculous actions. Should set to variance
        self.outlimit = outlimit

        # timee steps for changing step size of PID response
        self.dt = dt
        self.samplingRate = samplingRate  # sample rate is for filtering

        self.cutoffFreq = cutoffFreq
        self.enableDFilter = enableDFilter

        if cutoffFreq != -1 or enableDFilter:
            raise NotImplementedError('Have not implemnted filtering yet')

    def reset(self):
        # internal variables
        self.error = 0
        self.error_prev = 0
        self.integral = 0
        self.deriv = 0

    def update(self, measured):

        # init
        self.out = 0.

        # update error
        self.error_prev = self.error

        # calc new error
        self.error = self.desired - measured

        # proportional gain is easy
        self.out += self.kp * self.error

        # calculate deriv term
        self.deriv = (self.error - self.error_prev) / self.dt

        # filtter if needed (DT function_)
        if self.enableDFilter:
            print('Do Filter')
            self.deriv = self.deriv

        # calcualte error value added
        self.out += self.deriv * self.kd

        # accumualte normalized eerror
        self.integral = self.error * self.dt

        # limitt the integral term
        if self.ilimit != 0:
            self.integral = np.clip(self.integral, -self.ilimit, self.ilimit)

        self.out += self.ki * self.integral

        # limitt the total output
        if self.outlimit != 0:
            self.out = np.clip(self.out, -self.outlimit, self.outlimit)

        return self.out

In [11]:

# need info about initial condition of orbit

# v = np.sqrt(mu/r)

# low orbit: 180-20000 km
# mid orbit: 2000-35780 km
# high orbit: >35,780 km

# https://en.wikipedia.org/wiki/Orbital_speed

# some targets in solar sail angle at different places in orbit
# XY Plane / polar works. 
# 
targets_visual =  np.array([[90, -90], 
            [135, -67.5], 
            [180, -45],
            [225, -22.5],
            [270, 0],
            [315, 22.5],
            [0, 45], 
            [45, 67.5], 
            [89.9, 90]])

targets_actual = targets_visual - np.array([90,0])
print(targets_actual)
            
          
print([(angle-90)/2 - 90 for angle in [90, 180, 270, 360, 450]])          

[[ 0.00e+00 -9.00e+01]
 [ 4.50e+01 -6.75e+01]
 [ 9.00e+01 -4.50e+01]
 [ 1.35e+02 -2.25e+01]
 [ 1.80e+02  0.00e+00]
 [ 2.25e+02  2.25e+01]
 [-9.00e+01  4.50e+01]
 [-4.50e+01  6.75e+01]
 [-1.00e-01  9.00e+01]]
[-90.0, -45.0, 0.0, 45.0, 90.0]


In [13]:
import math

mu = 3.986004418*10**14 # SGP earth


def grav(x,y, mass1, mass2):
    d = np.sqrt(x**2+y**2)
    f = G * mass1 * mass2 / (d**2)

    # Compute the direction of the force.
    theta = math.atan2(y, x)
    fx = math.cos(theta) * f
    fy = math.sin(theta) * f
    return -fx, -fy
    
def earth2clock(angle):
    # convert from earth position to desired clock angle.
    # to start with, will just use this as the actual angle
    angle = np.rad2deg(angle)
    while angle < 90:
        angle += 360
    return (angle-90)/2 - 90
    
def clock2force(angle):
    # for now assumes the y distance from the sun line is 0
    force_mag = P_ss*Ap_ss*(math.cos(angle)**2)
    return force_mag*math.cos(angle), force_mag*math.sin(angle)
    
    
    # visualize
# from https://medium.com/analytics-vidhya/simulating-the-solar-system-with-under-100-lines-of-python-code-5c53b3039fc6
import plotly
import plotly.graph_objects as go

################################################# ###########
#################### ORBIT SIM, SWITHAROO ###################
######## ####################################################

init_orbit = 30000E3
# 1.496e+11 m in 1 AU
e = np.array([0,0])
# r = np.array([0, -6.684587e-5])*1.496e+11 # xy pos sail relative to earth, 10000km below in this diagram
r = np.array([0, init_orbit]) # xy pos sail relative to earth, 10000km below in this diagram
s = np.array([-1, 0])*1.496e+11 # sun is 1 AU to the "left" of earth

mu = 3.986004418*10**14 # SGP earth

m_ss = 0.001
m_earth =  5.972 * 10**24 

n_steps = 2000
t_vec = np.linspace(0,100000, n_steps)
v0 = np.sqrt(np.abs(mu/r[1]))
# TODO FIX velocity below

init_angle = 60
v0_sail = np.array([-v0*math.sin(np.deg2rad(init_angle)),v0*math.cos(np.deg2rad(init_angle))])
clock0 = 0

x = init_orbit*math.cos(np.deg2rad(init_angle))
y = init_orbit*math.sin(np.deg2rad(init_angle))
v = v0_sail
dt = 5 # seconds

# arrays to store and plot
Xs = []
Ys = []
F_sail = []
F_grav = []
Vs = []

earth_angle = math.atan2(y, x)
clock_angle = earth2clock(earth_angle)-15 # current hard code "control"
angular_rate = 0
for t in range(n_steps): #t_vec:
    print(f"===== Time {t*dt}(s) =====")
    control_x = 0.01
    sun2sail = r + np.array([x,y])
    earth_angle = math.atan2(y, x)
#     clock_angle = earth2clock(earth_angle) # current hard code "control"
    ix, iy, iz = inertials(control_x, 0, 0)
#     f = F_s(np.deg2rad(clock_angle))
    f_ss = np.array(clock2force(np.deg2rad(clock_angle)))
    f_vec = np.linalg.norm(f_ss)
    torque = -f_vec*control_x
    angular_accel = torque/ix
    angular_rate += angular_accel*dt
    clock_angle += np.rad2deg(angular_rate*dt)
    
    print(ix)
    f_ge = np.array(grav(x,y,m_ss,m_earth))
    f_gs = np.array([0,0 ]) # no sun gravity yet
    F_sail.append(f_ss)
    F_grav.append(F_grav)
                  
    x = x + v[0]*dt
    y = y + v[1]*dt
    Xs.append(x)
    Ys.append(y)
    f_tot = f_ss + f_ge + f_gs
    
                  
    v = v + (f_tot/m_ss)*dt
    Vs.append(v)
                  
    print(f"- Angle from earth to sail about orbit circle {earth_angle}")
    print(f"- Earth angle {np.rad2deg(earth_angle)}")
    print(f"- Clock angle {clock_angle}")
    print(f"- Angular Rate {angular_rate}")
    print(f"- Angular Accel {angular_accel}")
    
    print(f"- XY force sail {f_ss}")
    print(f"- XY force grav {f_ge}")
    print(f"- XY pos [{x/1000},{y/1000}] km")
    print(f"- Velocity at this step {v}")
    print(f"- Radius {np.sqrt(x**2+y**2)/1000} km")
    print()
    


===== Time 0(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.0471975511965976
- Earth angle 59.99999999999999
- Clock angle 59.99987165027968
- Angular Rate -4.480250427309344e-07
- Angular Accel -8.960500854618689e-08
- XY force sail [2.25000000e-08 3.89711432e-08]
- XY force grav [-0.00022144 -0.00038354]
- XY pos [14984.21629713518,25989.87483863097] km
- Velocity at this step [-3157.84764936  1820.627507  ]
- Radius 30000.005536116732 km

===== Time 5(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.047805066128379
- Earth angle 60.03480804158225
- Clock angle 59.999614949843036
- Angular Rate -8.960535621502714e-07
- Angular Accel -8.960570388386739e-08
- XY force sail [2.25002619e-08 3.89713952e-08]
- XY force grav [-0.0002212  -0.00038368]
- XY pos [14968.427058888392,25998.97797616598] km
- Velocity at this step [-3158.9535601   1818.70932287]
- Radius 30000.011073705056 km

===== Time 10(s) =====
0.005022040701754386

- Angular Rate -6.049001084530044e-05
- Angular Accel -9.575189890832517e-08
- XY force sail [2.48545087e-08 4.11656693e-08]
- XY force grav [-0.00019024 -0.00039991]
- XY pos [12870.899946027434,27099.532972710094] km
- Velocity at this step [-3292.6485415   1563.89587852]
- Radius 30000.745870055474 km

===== Time 660(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.1273894863940774
- Earth angle 64.59465943780218
- Clock angle 58.842974002166535
- Angular Rate -6.096925007345859e-05
- Angular Accel -9.584784563163065e-08
- XY force sail [2.48918757e-08 4.11993920e-08]
- XY force grav [-0.00018999 -0.00040003]
- XY pos [12854.436703319954,27107.35245210271] km
- Velocity at this step [-3293.59838068  1561.89594691]
- Radius 30000.751655953187 km

===== Time 665(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.1279970004671123
- Earth angle 64.62946743018188
- Clock angle 58.82537016812775
- Angular Rate -6.144897299030887e-0

- Earth angle 68.04064540476422
- Clock angle 56.406290450415895
- Angular Rate -0.00011148206590607419
- Angular Accel -1.0954295194410792e-07
- XY force sail [3.04131042e-08 4.58417283e-08]
- XY force grav [-0.0001656  -0.00041071]
- XY pos [11202.056876887647,27831.531662651465] km
- Velocity at this step [-3381.55903988  1361.17303306]
- Radius 30001.337186235498 km

===== Time 1160(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.1881407994218864
- Earth angle 68.07545327417377
- Clock angle 56.374196018629405
- Angular Rate -0.00011203070124619728
- Angular Accel -1.0972706802461791e-07
- XY force sail [3.04898124e-08 4.59017893e-08]
- XY force grav [-0.00016535 -0.00041081]
- XY pos [11185.14908168823,27838.337527816766] km
- Velocity at this step [-3382.38562974  1359.11921973]
- Radius 30001.343241465747 km

===== Time 1165(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.1887483113184518
- Earth angle 68.110261141850

- Clock angle 52.368522176579006
- Angular Rate -0.00017178641327013637
- Angular Accel -1.333243225380947e-07
- XY force sail [4.08364676e-08 5.30612023e-08]
- XY force grav [-0.00014035 -0.00041999]
- XY pos [9491.834686292972,28460.89642260525] km
- Velocity at this step [-3457.98909356  1153.43666626]
- Radius 30001.959117533956 km

===== Time 1660(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.2488918044461697
- Earth angle 71.55622946324326
- Clock angle 52.3191175948923
- Angular Rate -0.00017245452320071227
- Angular Accel -1.3362198611517973e-07
- XY force sail [4.09733028e-08 5.31444945e-08]
- XY force grav [-0.0001401  -0.00042007]
- XY pos [9474.544740825168,28466.663605936552] km
- Velocity at this step [-3458.68936838  1151.33657093]
- Radius 30001.965517269877 km

===== Time 1665(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.2494993122259577
- Earth angle 71.59103709504647
- Clock angle 52.26952118558549
- 

- Earth angle 75.69831133141598
- Clock angle 44.93337291653373
- Angular Rate -0.0002645830803161572
- Angular Accel -1.7915265073961847e-07
- XY force sail [6.36090555e-08 6.36294205e-08]
- XY force grav [-0.00010938 -0.00042907]
- XY pos [7393.84500023726,29077.421909066805] km
- Velocity at this step [-3532.83408597   898.61836446]
- Radius 30002.756686101555 km

===== Time 2260(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.3217922701189313
- Earth angle 75.73311847083085
- Clock angle 44.85731815091815
- Angular Rate -0.000265481214364889
- Angular Accel -1.796268097463587e-07
- XY force sail [6.38617514e-08 6.37133990e-08]
- XY force grav [-0.00010912 -0.00042914]
- XY pos [7376.180829807432,29081.91500088912] km
- Velocity at this step [-3533.37937511   896.47299468]
- Radius 30002.763601924376 km

===== Time 2265(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.3223997692107947
- Earth angle 75.76792560485265
- Cloc

...

- Radius 30012.66267152011 km

===== Time 7655(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.9771766461640328
- Earth angle 113.28387717703
- Clock angle -232.84040656384343
- Angular Rate -0.0014692420213814332
- Angular Accel -1.3331365333714117e-07
- XY force sail [-4.08315658e-08  5.30582135e-08]
- XY force grav [ 0.00017492 -0.00040646]
- XY pos [-11880.361783761515,27561.16183281362] km
- Velocity at this step [-3348.16768871 -1441.84447329]
- Radius 30012.6746173613 km

===== Time 7660(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 1.9777839608511054
- Earth angle 113.31867374543558
- Clock angle -233.26150071760188
- Angular Rate -0.0014698958887968416
- Angular Accel -1.307734830816679e-07
- XY force sail [-3.96701302e-08  5.23400723e-08]
- XY force grav [ 0.00017516 -0.00040636]
- XY pos [-11897.102622205051,27553.95261044718] km
- Velocity at this step [-3347.29207727 -1443.87599611]
- Radius 30012.686571882354 k

- Velocity at this step [-3249.54322507 -1652.11822736]
- Radius 30013.973290354133 km

===== Time 8185(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.0415505084884744
- Earth angle 116.97222779917674
- Clock angle -277.9510748704939
- Angular Rate -0.001490012615700428
- Angular Accel -6.145705273282683e-09
- XY force sail [4.04149163e-10 3.05982309e-09]
- XY force grav [ 0.00020068 -0.00039433]
- XY pos [-13629.342251538654,26740.987058918574] km
- Velocity at this step [-3248.539808   -1654.08988702]
- Radius 30013.986058083447 km

===== Time 8190(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.0421577939620383
- Earth angle 117.00702269377155
- Clock angle -278.37794186562155
- Angular Rate -0.0014900469066143507
- Angular Accel -6.858182784580196e-09
- XY force sail [4.76428434e-10 3.41109659e-09]
- XY force grav [ 0.00020092 -0.00039421]
- XY pos [-13645.584950578668,26732.716609483454] km
- Velocity at this step [-32

- XY force grav [ 0.00021771 -0.00038516]
- XY pos [-14785.622488059338,26120.51188494489] km
- Velocity at this step [-3173.16838873 -1794.38916728]
- Radius 30014.925845168324 km

===== Time 8550(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.085881526672575
- Earth angle 119.5122080426434
- Clock angle -309.264849685846
- Angular Rate -0.0015127669104392308
- Angular Accel -1.4091961403532347e-07
- XY force sail [4.43752954e-08 5.51296944e-08]
- XY force grav [ 0.00021795 -0.00038503]
- XY pos [-14801.488330002994,26111.539939108472] km
- Velocity at this step [-3172.07842906 -1796.31403947]
- Radius 30014.93919325628 km

===== Time 8555(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.086488788382089
- Earth angle 119.54700157565846
- Clock angle -309.6984311348217
- Angular Rate -0.001513484772038837
- Angular Accel -1.435723199212624e-07
- XY force sail [4.56341711e-08 5.58239003e-08]
- XY force grav [ 0.00021818 -0.00

- XY force grav [ 0.00023728 -0.00037339]
- XY pos [-16114.187072444027,25323.873261241108] km
- Velocity at this step [-3076.3670185  -1955.56124941]
- Radius 30016.088718504358 km

===== Time 8975(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.137497296726172
- Earth angle 122.46957382303225
- Clock angle -347.2403136839776
- Angular Rate -0.0016194970852093427
- Angular Accel -3.3966473391463277e-07
- XY force sail [1.6605799e-07 3.9020835e-08]
- XY force grav [ 0.0002375  -0.00037324]
- XY pos [-16129.568907536515,25314.09545499407] km
- Velocity at this step [-3075.17866987 -1957.42727094]
- Radius 30016.10270917129 km

===== Time 8980(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.138104521720118
- Earth angle 122.50436525240022
- Clock angle -347.70475377875795
- Angular Rate -0.0016212017664382122
- Angular Accel -3.409362457738915e-07
- XY force sail [1.66991302e-07 3.78159518e-08]
- XY force grav [ 0.00023773 -0.

- Angle from earth to sail about orbit circle 2.1939672259923593
- Earth angle 125.70506243938708
- Clock angle -392.5548861771195
- Angular Rate -0.001773840038750019
- Angular Accel -2.575077388120818e-07
- XY force sail [ 1.09614881e-07 -6.86193212e-08]
- XY force grav [ 0.00025817 -0.00035921]
- XY pos [-17533.355899799608,24364.46805751396] km
- Velocity at this step [-2959.77764429 -2127.74414946]
- Radius 30017.426152730946 km

===== Time 9445(s) =====
0.0050220407017543866
- Angle from earth to sail about orbit circle 2.194574408894924
- Earth angle 125.73985145709653
- Clock angle -393.0634186552621
- Angular Rate -0.001775113219382931
- Angular Accel -2.5463612658234403e-07
- XY force sail [ 1.07786438e-07 -6.88127824e-08]
- XY force grav [ 0.00025839 -0.00035905]
- XY pos [-17548.15478802105,24353.829336766677] km
- Velocity at this step [-2958.48517554 -2129.53976779]
- Radius 30017.4405942396 km

===== Time 9450(s) =====
0.0050220407017543866
- Angle from earth to sail abo

In [63]:
# STATIC PLOT CELL
import plotly.graph_objects as go
Vs = np.stack(Vs)

adjust = 1.5
xm = -adjust*init_orbit
xM = adjust*init_orbit
ym = -adjust*init_orbit
yM = adjust*init_orbit
# Create figure
fig = go.Figure(
    data=[go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="Traj.",
                     mode="lines",
                     line=dict(width=2, color="blue")),
          go.Scatter(x=[0], y=[0],
                     name="Earth",
                     mode="markers",
                     marker=dict(size=20, color="black")),
          go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="curve",
                     showlegend=False,
                     mode="lines",
                     line=dict(width=2, color="blue"))
          ],
    layout=go.Layout(width=800, height=800,
                     xaxis=dict(range=[xm, xM], autorange=False, zeroline=True),
                     yaxis=dict(range=[ym, yM], autorange=False, zeroline=True),
                     title=f"Animating Solar Sail Orbit, t:{dt*n_steps}s",
                     hovermode="closest",
                     xaxis_title="X Relative Position to Earth (m)",
                     yaxis_title="Y Relative Position to Earth (m)",
                     plot_bgcolor='white',
                    font=dict(family='Times New Roman', size=26, color='#000000'),

                    ), # was none
)
import os

fig.write_image(os.getcwd() + "/orbit.png")
# fig.show()

In [34]:

################################################# ###########
#################### ORBIT SIM, LONG ###################
######## ####################################################

init_orbit = 30000E3
# 1.496e+11 m in 1 AU
e = np.array([0,0])
# r = np.array([0, -6.684587e-5])*1.496e+11 # xy pos sail relative to earth, 10000km below in this diagram
r = np.array([0, -init_orbit]) # xy pos sail relative to earth, 10000km below in this diagram
s = np.array([-1, 0])*1.496e+11 # sun is 1 AU to the "left" of earth

mu = 3.986004418*10**14 # SGP earth

m_ss = 0.001
m_earth =  5.972 * 10**24 

n_steps = 10000
t_vec = np.linspace(0,100000, n_steps)
v0 = np.sqrt(np.abs(mu/r[1]))
v0_sail = np.array([v0,0])
clock0 = 0

x,y = r
v = v0_sail
dt = 60 # seconds

# arrays to store and plot
Xs = []
Ys = []
F_sail = []
F_grav = []
Vs = []

# TODO switcharoo logic
# From 70-90 degress, full torque in the opposite direction.
# Go to 0 full torque, switch direction to break (do not want to overshoot this)
# check deviation from nominal orbit

for t in range(n_steps): #t_vec:
    print(f"===== Time {t*dt}(s) =====")
    sun2sail = r + np.array([x,y])
    earth_angle = math.atan2(y, x)
    clock_angle = earth2clock(earth_angle) # current hard code "control"

    f_ss = np.array(clock2force(np.deg2rad(clock_angle)))
    f_ge = np.array(grav(x,y,m_ss,m_earth))
    f_gs = np.array([0,0 ]) # no sun gravity yet
    F_sail.append(f_ss)
    F_grav.append(F_grav)
                  
    x = x + v[0]*dt
    y = y + v[1]*dt
    Xs.append(x)
    Ys.append(y)
    f_tot = f_ss + f_ge + f_gs
    
                  
    v = v + (f_tot/m_ss)*dt
    Vs.append(v)
                  
    print(f"- Angle from earth to sail about orbit circle {earth_angle}")
    print(f"- Earth angle {np.rad2deg(earth_angle)}")
    print(f"- Clock angle {clock_angle}")
    print(f"- XY force sail {f_ss}")
    print(f"- XY force grav {f_ge}")
    print(f"- XY pos [{x/1000},{y/1000}] km")
    print(f"- Velocity at this step {v}")
    print(f"- Radius {np.sqrt(x**2+y**2)/1000} km")
    print()

===== Time 0(s) =====
- Angle from earth to sail about orbit circle -1.5707963267948966
- Earth angle -90.0
- Clock angle 0.0
- XY force sail [1.8e-07 0.0e+00]
- XY force grav [-2.71183067e-20  4.42875557e-04]
- XY pos [218.70540234754148,-30000.0] km
- Velocity at this step [3645.10083913   26.57253344]
- Radius 30000.797190291727 km

===== Time 60(s) =====
- Angle from earth to sail about orbit circle -1.5635062758622604
- Earth angle -89.58231084912454
- Clock angle 0.20884457543772328
- XY force sail [1.79996413e-07 6.56094414e-10]
- XY force grav [-3.22838519e-06  4.42840254e-04]
- XY pos [437.4114526950829,-29998.4056479936] km
- Velocity at this step [3644.9179358    53.14298802]
- Radius 30001.59446097029 km

===== Time 120(s) =====
- Angle from earth to sail about orbit circle -1.5562162033572495
- Earth angle -89.16462046224305
- Clock angle 0.41768976887846065
- XY force sail [1.79985651e-07 1.31212975e-09]
- XY force grav [-6.45626522e-06  4.42781417e-04]
- XY pos [656.1065

- XY force sail [1.09329817e-07 6.86517277e-08]
- XY force grav [-0.00039363  0.00018985]
- XY pos [27298.39575372229,-12922.696942905231] km
- Velocity at this step [1584.5949905  3290.15461271]
- Radius 30202.624174151082 km

===== Time 9300(s) =====
- Angle from earth to sail about orbit circle -0.4421311895362249
- Earth angle -25.33225115152435
- Clock angle 32.33387442423782
- XY force sail [1.08582292e-07 6.87327611e-08]
- XY force grav [-0.00039494  0.00018696]
- XY pos [27393.4714531524,-12725.287666142593] km
- Velocity at this step [1560.90531335 3301.37619838]
- Radius 30204.887426387737 km

===== Time 9360(s) =====
- Angle from earth to sail about orbit circle -0.4348771180375628
- Earth angle -24.916623470364872
- Clock angle 32.541688264817566
- XY force sail [1.07833989e-07 6.88081817e-08]
- XY force grav [-0.00039622  0.00018406]
- XY pos [27487.1257719537,-12527.205094239642] km
- Velocity at this step [1537.1384063  3312.42394589]
- Radius 30207.167207077608 km

====

- XY force grav [-0.00036466 -0.00021595]
- XY pos [26280.29806533972,15815.596816455494] km
- Velocity at this step [-1813.48465039  3135.46238989]
- Radius 30672.254059064133 km

===== Time 17520(s) =====
- Angle from earth to sail about orbit circle 0.5417451476089142
- Earth angle 31.039710529682587
- Clock angle 60.51985526484128
- XY force sail [2.14531282e-08 3.79489541e-08]
- XY force grav [-0.00036301 -0.00021846]
- XY pos [26171.488986316035,16003.724559849163] km
- Velocity at this step [-1835.26390506  3122.35704273]
- Radius 30676.799630150163 km

===== Time 17580(s) =====
- Angle from earth to sail about orbit circle 0.5488285795017326
- Earth angle 31.445561281609443
- Clock angle 60.72278064080473
- XY force sail [2.10520380e-08 3.75492648e-08]
- XY force grav [-0.00036135 -0.00022096]
- XY pos [26061.373152012562,16191.065982412883] km
- Velocity at this step [-1856.94336462  3109.10165053]
- Radius 30681.35896949952 km

===== Time 17640(s) =====
- Angle from earth to 

- XY force sail [4.99208833e-10 3.51789649e-09]
- XY force grav [-0.00011379 -0.00039285]
- XY pos [8480.183508693954,30049.40317666993] km
- Velocity at this step [-3420.63179423  1047.00419882]
- Radius 31223.07069484335 km

===== Time 24000(s) =====
- Angle from earth to sail about orbit circle 1.2957412745768697
- Earth angle 74.2405063741566
- Clock angle 82.1202531870783
- XY force sail [4.63801043e-10 3.35113471e-09]
- XY force grav [-0.00011105 -0.00039349]
- XY pos [8274.945601039904,30112.223428599107] km
- Velocity at this step [-3427.29452204  1023.39502516]
- Radius 31228.52421287376 km

===== Time 24060(s) =====
- Angle from earth to sail about orbit circle 1.3026127721869092
- Earth angle 74.63421418614608
- Clock angle 82.31710709307305
- XY force sail [4.30102696e-10 3.18827727e-09]
- XY force grav [-0.0001083  -0.00039411]
- XY pos [8069.307929717746,30173.6271301089] km
- Velocity at this step [-3433.79259392   999.74887738]
- Radius 31233.979968160475 km

===== Time

- XY force sail [ 4.24067470e-09 -1.41718269e-08]
- XY force grav [ 0.00021522 -0.00032742]
- XY pos [-17698.073878594423,26539.839039212882] km
- Velocity at this step [-2967.52528731 -1896.44599769]
- Radius 31899.60619254593 km

===== Time 31680(s) =====
- Angle from earth to sail about orbit circle 2.1589253788335965
- Earth angle 123.69731249084747
- Clock angle -73.15134375457626
- XY force sail [ 4.38296915e-09 -1.44726645e-08]
- XY force grav [ 0.00021732 -0.00032589]
- XY pos [-17876.12539583282,26426.05227935165] km
- Velocity at this step [-2954.48598754 -1916.00006375]
- Radius 31904.421296092576 km

===== Time 31740(s) =====
- Angle from earth to sail about orbit circle 2.165547231605258
- Earth angle 124.0767167072207
- Clock angle -72.96164164638965
- XY force sail [ 4.52822636e-09 -1.47757739e-08]
- XY force grav [ 0.0002194  -0.00032434]
- XY pos [-18053.394555085513,26311.092275526822] km
- Velocity at this step [-2941.32146196 -1935.46150194]
- Radius 31909.224868255

...

- Velocity at this step [1212.70007395 2675.07452193]
- Radius 47348.145793933676 km

===== Time 563760(s) =====
- Angle from earth to sail about orbit circle -0.4028453800682369
- Earth angle -23.08134007425355
- Clock angle 33.45932996287323
- XY force sail [1.04521090e-07 6.90743555e-08]
- XY force grav [-1.63561892e-04  6.97021083e-05]
- XY pos [43630.651974504704,-18401.74570152329] km
- Velocity at this step [1202.89263168 2679.26079289]
- Radius 47352.48712141615 km

===== Time 563820(s) =====
- Angle from earth to sail about orbit circle -0.39912473480623045
- Earth angle -22.868162803675233
- Clock angle 33.5659185981624
- XY force sail [1.04135521e-07 6.90982232e-08]
- XY force grav [-1.63790059e-04  6.90804030e-05]
- XY pos [43702.82553240555,-18240.990053950067] km
- Velocity at this step [1193.07147625 2683.40976296]
- Radius 47356.84404248433 km

===== Time 563880(s) =====
- Angle from earth to sail about orbit circle -0.3954047147220372
- Earth angle -22.65502135314706
-

- XY force sail [4.95400352e-08 5.78460801e-08]
- XY force grav [-1.69819004e-04 -2.64282529e-05]
- XY pos [47564.48750413675,7577.967681115369] km
- Velocity at this step [-359.59751758 2872.31698134]
- Radius 48164.36510229539 km

===== Time 572940(s) =====
- Angle from earth to sail about orbit circle 0.1579920327999088
- Earth angle 9.052276676127246
- Clock angle 49.52613833806362
- XY force sail [4.92276957e-08 5.76914993e-08]
- XY force grav [-1.69679558e-04 -2.70333241e-05]
- XY pos [47542.91165308195,7750.30669999556] km
- Velocity at this step [-369.77533738 2870.69844338]
- Radius 48170.48580195919 km

===== Time 573000(s) =====
- Angle from earth to sail about orbit circle 0.16159564177758926
- Earth angle 9.258748261563788
- Clock angle 49.62937413078188
- XY force sail [4.89162688e-08 5.75361588e-08]
- XY force grav [-1.69537946e-04 -2.76375812e-05]
- XY pos [47520.72513283906,7922.548606598523] km
- Velocity at this step [-379.94467919 2869.04364068]
- Radius 48176.61355

- XY force sail [1.81983837e-08 3.45663663e-08]
- XY force grav [-1.37069817e-04 -9.40945200e-05]
- XY pos [40275.436624501286,27855.39787253541] km
- Velocity at this step [-1536.43615681  2402.93593495]
- Radius 48969.72519763073 km

===== Time 580500(s) =====
- Angle from earth to sail about orbit circle 0.6050813201166257
- Earth angle 34.668605904886974
- Clock angle 62.334302952443494
- XY force sail [1.80178052e-08 3.43688415e-08]
- XY force grav [-1.36704080e-04 -9.45476169e-05]
- XY pos [40183.250455092806,27999.57402863251] km
- Velocity at this step [-1544.63732057  2397.26514007]
- Radius 48976.216298542175 km

===== Time 580560(s) =====
- Angle from earth to sail about orbit circle 0.6085731585104541
- Earth angle 34.868673507595076
- Clock angle 62.43433675379754
- XY force sail [1.78383066e-08 3.41713956e-08]
- XY force grav [-1.36336956e-04 -9.49992015e-05]
- XY pos [40090.57221585883,28143.40993703669] km
- Velocity at this step [-1552.81646766  2391.56723827]
- Radius

- XY pos [22946.080553877648,44255.30604591993] km
- Velocity at this step [-2448.31212181  1371.30505493]
- Radius 49850.32322867204 km

===== Time 589020(s) =====
- Angle from earth to sail about orbit circle 1.0924637548752156
- Earth angle 62.59356242536437
- Clock angle 76.29678121268219
- XY force sail [2.39291725e-09 9.81374502e-09]
- XY force grav [-7.38293083e-05 -1.42392014e-04]
- XY pos [22799.181826568783,44337.5843492156] km
- Velocity at this step [-2452.74173674  1362.76212289]
- Radius 49856.03351536053 km

===== Time 589080(s) =====
- Angle from earth to sail about orbit circle 1.0958391605394902
- Earth angle 62.786958924071854
- Clock angle 76.39347946203594
- XY force sail [2.34356226e-09 9.68230394e-09]
- XY force grav [-7.33314568e-05 -1.42607734e-04]
- XY pos [22652.01732236468,44419.35007658897] km
- Velocity at this step [-2457.14148353  1354.20623981]
- Radius 49861.734326026744 km

===== Time 589140(s) =====
- Angle from earth to sail about orbit circle 1.099

- XY force sail [1.06911547e-11 2.73806084e-10]
- XY force grav [-1.22085401e-05 -1.56095210e-04]
- XY pos [3768.51109447796,50318.451613378515] km
- Velocity at this step [-2762.00796078   273.20825003]
- Radius 50459.37225766011 km

===== Time 596280(s) =====
- Angle from earth to sail about orbit circle 1.4960426581508461
- Earth angle 85.71693028357647
- Clock angle 87.85846514178823
- XY force sail [9.39240209e-12 2.51172365e-10]
- XY force grav [-1.16914530e-05 -1.56108288e-04]
- XY pos [3602.790616830865,50334.84410838029] km
- Velocity at this step [-2762.7094474    263.84176784]
- Radius 50463.616910043915 km

===== Time 596340(s) =====
- Angle from earth to sail about orbit circle 1.499341712625861
- Earth angle 85.90595218137857
- Clock angle 87.95297609068928
- XY force sail [8.20344303e-12 2.29514984e-10]
- XY force grav [-1.11745005e-05 -1.56119742e-04]
- XY pos [3437.028049986656,50350.67461445085] km
- Velocity at this step [-2763.37991694   254.47459709]
- Radius 50467

In [4]:
# ANIMATION CELL
import plotly.graph_objects as go
Vs = np.stack(Vs)

adjust = 4
xm = -adjust*init_orbit
xM = adjust*init_orbit
ym = -adjust*init_orbit
yM = adjust*init_orbit
# Create figure
fig = go.Figure(
    data=[go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="Traj.",
                     mode="lines",
                     line=dict(width=2, color="blue")),
          go.Scatter(x=[0], y=[0],
                     name="Earth",
                     mode="markers",
                     marker=dict(size=20, color="black")),
          go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="curve",
                     showlegend=False,
                     mode="lines",
                     line=dict(width=2, color="blue"))
          ],
    layout=go.Layout(width=600, height=600,
                     xaxis=dict(range=[xm, xM], autorange=False, zeroline=False),
                     yaxis=dict(range=[ym, yM], autorange=False, zeroline=False),
                     title="Animating Solar Sail Orbit + Forces",
                     hovermode="closest",
                     updatemenus=[dict(type="buttons",
                                       buttons=[{
                                            "args": [None, {"frame": {"duration": 50, "redraw": False},
                                                            "fromcurrent": True, "transition": {"duration": 30,
                                                                                                "easing": "quadratic-in-out"}}],
                                            "label": "Play",
                                            "method": "animate"
                                        },
                                        {
                                            "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                                              "mode": "immediate",
                                                              "transition": {"duration": 0}}],
                                            "label": "Pause",
                                            "method": "animate"
                                        },
#                                        {
#                                         "args": [None, {"frame": {"duration": 50, "redraw": True},
#                                                         "fromcurrent": False, "transition": {"duration": 30,
#                                                                                             "easing": "quadratic-in-out"}}],
#                                         "label": "Reset",
#                                         "method": "animate"
#                                     },
                                    ],
                                       direction= "left",
                                    pad= {"r": 10, "t": 70},
                                    x= 0.1,
                                    y= 0,
                                    )]
                    ), # was none

    frames=[go.Frame(
        data=[go.Scatter(
            x=[Xs[k], Xs[k]+1000*Vs[k,0], None, Xs[k], Xs[k]+1000*Vs[k,0]],
            y=[Ys[k], Ys[k]+1000*Vs[k,1], None, Ys[k], Ys[k]+1000*Vs[k,1]],
#             x=[xx[k], xend[k], None, xx[k], xnoe[k]],
#             y=[yy[k], yend[k], None, yy[k], ynoe[k]],
            mode="lines",
            line=dict(color="red", width=4))
        ], 
        name=str(k)) for k in range(n_steps)]
)

def frame_args(duration):
    return {
            "frame": {"duration": duration},
            "mode": "immediate",
            "fromcurrent": True,
            "transition": {"duration": duration, "easing": "linear"},
        }
sliders = [
            {
                "pad": {"b": 10, "t": 60},
                "len": 0.7,
                "x": 0.2,
                "y": 0,
                "steps": [
                    {
                        "args": [[f.name], frame_args(0)],
                        "label": str(k),
                        "method": "animate",
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]
                                
fig.update_layout(sliders=sliders)

fig.show()

NameError: name 'Vs' is not defined

In [5]:
import numpy as np
import torch
import torch.optim as optim
import math
import gym
from gym import spaces, logger
from gym.utils import seeding


class RigidEnv(gym.Env):
    """
    Source:
        This file is created by Nathan Lambert, adapted from a model from Somil Bansal
    Observation: 
        Type: Box(12)
        Num	Observation                 Min         Max
        0	x-pos                       -10         10      (meters)
        1	y-pos                       -10         10      (meters)
        2	z-pos                       -10         10      (meters)
        3	x-vel                       -Inf        Inf     (meters/sec)
        4   y-vel                       -Inf        Inf     (meters/sec)
        5   z-vel                       -Inf        Inf     (meters/sec)
        6   roll                        -180        180     (degrees)
        7   pitch                       -90         90      (degrees)
        8   yaw                         -180        180     (degrees)
        9   omega_x                     -Inf        Inf     (rad/s^2)
        10  omega_y                     -Inf        Inf     (rad/s^2)
        11  omega_z                     -Inf        Inf     (rad/s^2)
    """

    def __init__(self, dt=.01, x_noise=0.0, u_noise=0): #0.01 noise
        self.x_dim = 12
        self.u_dim = 4
        self.dt = dt
        self.x_noise = x_noise

        # simulate ten steps per return
        self.dt = self.dt

        # Setup the state indices
        self.idx_xyz = [0, 1, 2]
        self.idx_xyz_dot = [3, 4, 5]
        self.idx_ptp = [6, 7, 8]
        self.idx_ptp_dot = [9, 10, 11]

        self.seed()
        self.viewer = None
        self.state = None
        self.steps_beyond_done = None

    def seed(self, seed=None, inertial=False):
        self.np_random, seed = seeding.np_random(seed)
        if inertial:
            self.Ixx = self.Ixx * self.np_random.uniform(low=0.85, high=1.15, size=1)[0]
            self.Iyy = self.Iyy * self.np_random.uniform(low=0.85, high=1.15, size=1)[0]

        return [seed]

    def step(self, forces, torques):
        # assert self.action_space.contains(u), "%r (%s) invalid" % (u, type(u))

        # We need to convert from upright orientation to N-E-Down that the simulator runs in
        # For reference, a negative thrust of -mg/4 will keep the robot stable
        u = self.pwm_thrust_torque(pwm)
        state = self.state
        self.last_state = state

        dt = self.dt
        u0 = u
        x0 = state
        idx_xyz = self.idx_xyz
        idx_xyz_dot = self.idx_xyz_dot
        idx_ptp = self.idx_ptp
        idx_ptp_dot = self.idx_ptp_dot

        m = self.m
        L = self.L
        Ixx = self.Ixx
        Iyy = self.Iyy
        Izz = self.Izz
        g = self.g
        
        # Cross term, direct term for the three torques
        Tx = np.array([Iyy / Ixx - Izz / Ixx, L / Ixx])
        Ty = np.array([Izz / Iyy - Ixx / Iyy, L / Iyy])
        Tz = np.array([Ixx / Izz - Iyy / Izz, 1. / Izz])

        # # Add noise to input
        # u_noise_vec = np.random.normal(
        #     loc=0, scale=self.u_noise, size=(self.u_dim))
        # u = u+u_noise_vec

        # Array containing the forces
        # This assumes the force all comes directly out of the plane
        # Third column of Qb/i (converts body forces to inertial frame)
        Fxyz = np.zeros(3)
        Fxyz[0] = -1 * (math.cos(x0[idx_ptp[0]]) * math.sin(x0[idx_ptp[1]]) * math.cos(x0[idx_ptp[2]]) + math.sin(x0[idx_ptp[0]]) * math.sin(x0[idx_ptp[2]])) * u0[0] / m
        Fxyz[1] = -1 * (math.cos(x0[idx_ptp[0]]) * math.sin(x0[idx_ptp[1]]) * math.sin(x0[idx_ptp[2]]) - math.sin(x0[idx_ptp[0]]) * math.cos(x0[idx_ptp[2]])) * u0[0] / m
        Fxyz[2] = g - 1 * (math.cos(x0[idx_ptp[0]]) * math.cos(x0[idx_ptp[1]])) * u0[0] / m

        # Compute the torques
        t0 = np.array([x0[idx_ptp_dot[1]] * x0[idx_ptp_dot[2]], u0[1]])
        t1 = np.array([x0[idx_ptp_dot[0]] * x0[idx_ptp_dot[2]], u0[2]])
        t2 = np.array([x0[idx_ptp_dot[0]] * x0[idx_ptp_dot[1]], u0[3]])
        Txyz = np.array([Tx.dot(t0), Ty.dot(t1), Tz.dot(t2)])

        x1 = np.zeros(12)
        x1[idx_xyz_dot] = x0[idx_xyz_dot] + dt * Fxyz
        x1[idx_ptp_dot] = x0[idx_ptp_dot] + dt * Txyz
        x1[idx_xyz] = x0[idx_xyz] + dt * x0[idx_xyz_dot]
        x1[idx_ptp] = x0[idx_ptp] + dt * self.pqr2rpy(x0[idx_ptp], x0[idx_ptp_dot])

        # makes states less than 1e-12 = 0
        x1[abs(x1) < 1e-15] = 0
        self.state = x1
        state = x1

        # Add noise component
        x_noise_vec = np.random.normal(
            loc=0, scale=self.x_noise, size=(self.x_dim))

        self.state += x_noise_vec

        obs = self.get_obs()
        reward = self.get_reward(obs, u)
        done = self.get_done(obs)

        return obs, reward, done, {}

    def get_obs(self):
        raise NotImplementedError("Subclass must implement this function")

    def set_state(self, x):
        self.state = x

    def reset(self, safe=False):
        x0 = np.array([0, 0, 0])
        v0 = self.np_random.uniform(low=-0.01, high=0.01, size=(3,))
        # ypr0 = self.np_random.uniform(low=-0.0, high=0.0, size=(3,))
        if safe:
            ypr0 = self.np_random.uniform(low=-0.01, high=0.01, size=(3,))
            ypr0 = self.np_random.uniform(low=-0.00, high=0.00, size=(3,))
            w0 = self.np_random.uniform(low=-0.00, high=0.00, size=(3,))
        else:
            ypr0 = self.np_random.uniform(low=-np.pi/16., high=np.pi/16., size=(3,))
            w0 = self.np_random.uniform(low=-0.01, high=0.01, size=(3,))

        ypr0[-1] = 0 # 0 out yaw

        self.state = np.concatenate([x0, v0, ypr0, w0])
        self.last_state = self.state
        self.steps_beyond_done = None
        self.interal = 0

        return self.get_obs()

    def get_done(self, state):
        # Done is pitch or roll > 35 deg
        max_a = np.deg2rad(45)
        d = (abs(state[1]) > max_a) or (abs(state[0]) > max_a)
        return d

    def pqr2rpy(self, x0, pqr):
        rotn_matrix = np.array([[1., math.sin(x0[0]) * math.tan(x0[1]), math.cos(x0[0]) * math.tan(x0[1])],
                                [0., math.cos(x0[0]), -math.sin(x0[0])],
                                [0., math.sin(x0[0]) / math.cos(x0[1]), math.cos(x0[0]) / math.cos(x0[1])]])
        return rotn_matrix.dot(pqr)


